# Interactive dashboard

In [1]:
import pandas as pd
import geopandas as gpd
import altair as alt

In [3]:
municipios = pd.read_csv('data/municipios.csv')

In [4]:
municipios.head()


Comunidad Provincia  Población   Latitud   Longitud   Altitud  Habitantes  \
0  Andalucía   Almería       Abla  37,14114  -2,780104  871,1684        1504   
1  Andalucía   Almería   Abrucena  37,13305  -2,797098  976,9387        1341   
2  Andalucía   Almería       Adra  36,74807  -3,022522  10,97898       24373   
3  Andalucía   Almería  Albánchez   37,2871  -2,181163  481,3123         815   
4  Andalucía   Almería  Alboloduy  37,03319   -2,62175  388,4346         674   

   Hombres  Mujeres Capital  
0      783      721      No  
1      682      659      No  
2    12338    12035      No  
3      422      393      No  
4      334      340      No

In [9]:
municipios.Longitud = municipios.Longitud.str.replace(',','.').astype(float)
municipios.Latitud = municipios.Latitud.str.replace(',','.').astype(float)

In [13]:
municipios1000 = municipios.get(municipios.Habitantes > 1000)
municipios1000.to_csv('data/municipios1000.csv', index=False, sep=',')

In [11]:
alt.Chart(municipios1000).mark_point().encode(
    x='Longitud:Q',
    y='Latitud:Q')


alt.Chart(...)


    alt.Chart is used to declare the chart
    municipios is the data (could also be a path to our file)
    mark_point is the type of marker we’re using. We’ll later see mark_circle or mark_square
    encode is used to encode the variables
    x='x:Q' means that we encode the column x to being quantitative. Same for the y column.
    
There is a major issue with the graph above, the origin of the plot is (0,0). We need to change that. We will also delete the axis values Notice how we now declare the axis as objects in Altair using alt.X and alt.Y. We also disable the zero scale.


In [53]:
alt.Chart(municipios1000).mark_point().encode(
    x=alt.X('Longitud:Q', axis=None),
    y=alt.Y('Latitud:Q', axis=None, scale=alt.Scale(zero=False)))

alt.Chart(...)

The points above are a bit too big. Let’s reduce their size in the mark_point. We will also assign the graph to a variable, and call that variable. We are also maxing the graph a bit bigger 

In [18]:
alt.Chart(municipios1000,  width=800, height=800).mark_point(size=1).encode(
    x=alt.X('Longitud:Q', axis=None),
    y=alt.Y('Latitud:Q', axis=None, scale=alt.Scale(zero=False)))

alt.Chart(...)

In [ ]:
Let’s now set the size of the marks accordingly to the population of the city.

In [21]:
alt.Chart(municipios1000,  width=800, height=800).mark_point(size=1).encode(
    x=alt.X('Longitud:Q', axis=None),
    y=alt.Y('Latitud:Q', axis=None, scale=alt.Scale(zero=False)),
    size='Habitantes:Q',)

alt.Chart(...)

The first step toward developing interactive charts is to integrate tooltips. Tooltips display a certain text message on overlay. For example :

In [23]:
map = alt.Chart(municipios1000,  width=800, height=800).mark_point(size=1).encode(
    x=alt.X('Longitud:Q', axis=None),
    y=alt.Y('Latitud:Q', axis=None, scale=alt.Scale(zero=False)),
    size='Habitantes:Q',
    tooltip=['Provincia:N', 'Población:N', 'Habitantes:Q'],)

display(map)

alt.Chart(...)

# Selection intervals

In some cases, you might want to select a specific region of the map. This is done by adding a selection interval on the map :




In [32]:
brush = alt.selection_interval()
map.add_selection(brush)

alt.Chart(...)

# Histograms

In [48]:

population = alt.Chart(municipios1000, width=800, height=100).mark_bar().encode(
    x=alt.X('Habitantes:Q', bin=alt.Bin(maxbins=60)),
    y='sum(Habitantes):Q'
)

display(population)

alt.Chart(...)

In [37]:
population = alt.Chart(municipios1000, width=800, height=100).mark_bar().encode(
    x='Provincia:N',
    y='sum(Habitantes):Q'
    )

display(population)

alt.Chart(...)

# Transform filters

At that point, this is a cool feature, but it remains useless. What we might want to do is on the Dashboard, when a region is selected on the map, update it on the histograms (to get for example the population’s histogram in this region).

This can be achieved using transform_filter.

In [50]:
brush = alt.selection_interval()
map = alt.Chart(municipios1000,  width=800, height=800).mark_point(size=1).encode(
    x=alt.X('Longitud:Q', axis=None),
    y=alt.Y('Latitud:Q', axis=None, scale=alt.Scale(zero=False)),
    size='Habitantes:Q',
    color=alt.condition(brush, 'Habitantes:Q', alt.value('lightgrey'), scale=alt.Scale(scheme='viridis', domain=[0,200000])),
    tooltip=['Provincia:N', 'Población:N', 'Habitantes:Q']).add_selection(brush)


population = alt.Chart(municipios1000, width=800, height=100).mark_bar().encode(
    x=alt.X('Habitantes:Q', bin=alt.Bin(maxbins=60)),
    y='sum(Habitantes):Q'
    ).transform_filter(brush)

population & map

alt.VConcatChart(...)

 The last improvement we’ll explore is to update the view in both ways. If we select a region of the histogram, it will update the map.

In [51]:
brush = alt.selection_interval()
pop_selection = alt.selection_interval(encodings=['x'])

map = alt.Chart(municipios1000,  width=800, height=800).mark_point(size=1).encode(
    x=alt.X('Longitud:Q', axis=None),
    y=alt.Y('Latitud:Q', axis=None, scale=alt.Scale(zero=False)),
    size='Habitantes:Q',
    color=alt.condition(pop_selection, 'Habitantes:Q', alt.value('lightgrey'), scale=alt.Scale(scheme='viridis', domain=[0,200000])),
    tooltip=['Provincia:N', 'Población:N', 'Habitantes:Q']).add_selection(brush)


population = alt.Chart(municipios1000, width=800, height=100).mark_bar().encode(
    x=alt.X('Habitantes:Q', bin=alt.Bin(maxbins=60)),
    y='sum(Habitantes):Q'
    ).add_selection(pop_selection).transform_filter(brush)

population & map

alt.VConcatChart(...)